# Portfolio Scenario Analysis

## 1. Import Portofolio data

In [1]:
import numpy as np
import pandas as pd
import time
import yfinance as yf
import matplotlib.pyplot as plt
import functions as f
import pulp


%load_ext autoreload
%autoreload 2

In [2]:
data = {
    "strike": [630.0, 375.0, 37.0],
    "lastPrice": [67.25, 21.50, 0.61],
    "impliedVolatility": [0.140634, 0.214951, 0.263679],
    "expiration": ["2024-12-27", "2026-06-18", "2026-06-18"],
    "time_to_expiration": [0.093744, 1.567716, 1.567716],
    "blackScholes_Price": [73.14, 19.50, 0.88],
    "delta": [-0.997829, -0.254040, 0.212588],
    "vega": [1.160627, 165.448887, 9.337046],
    "gamma": [0.000286, 0.002888, 0.034225],
    "theta": [17.940647, -7.615076, -0.922608],
    "rho": [-58.781247, -194.780122, 7.179852],
    "type": ["put", "put", "call"],
    "stock": ["META", "MSFT", "PFE"],
    "spot_price": [555.11, 412.32, 25.69],
    "initial_weight": [0.000035, 0.000035, 0.000035],
    "market_price": [67.25, 21.50, 0.61],
    "expected_return": [5.89, -2.00, 0.27],
    "optimized_N": [9, 15, 60]
}


index = [14974, 18613, 24168]
start_portfolio_df = pd.DataFrame(data, index=index).reset_index(drop=True)

In [3]:
portfolio_df = start_portfolio_df

In [4]:
portfolio_df

strike  lastPrice  impliedVolatility  expiration  time_to_expiration  \
0   630.0      67.25           0.140634  2024-12-27            0.093744   
1   375.0      21.50           0.214951  2026-06-18            1.567716   
2    37.0       0.61           0.263679  2026-06-18            1.567716   

   blackScholes_Price     delta        vega     gamma      theta         rho  \
0               73.14 -0.997829    1.160627  0.000286  17.940647  -58.781247   
1               19.50 -0.254040  165.448887  0.002888  -7.615076 -194.780122   
2                0.88  0.212588    9.337046  0.034225  -0.922608    7.179852   

   type stock  spot_price  initial_weight  market_price  expected_return  \
0   put  META      555.11        0.000035         67.25             5.89   
1   put  MSFT      412.32        0.000035         21.50            -2.00   
2  call   PFE       25.69        0.000035          0.61             0.27   

   optimized_N  
0            9  
1           15  
2           60

total_delta   total_vega  total_gamma  total_theta    total_rho  \
0      -3.5781  305240.1708     209.9394    -811.6797 -301994.1933   

   total_expected_return  total_cost  
0                 3921.0     96435.0

## 2. Scenarios

## a. Spot Price Changes

    Upward Movement: Increase the underlying stock prices by 5%, 10%, 20%, etc.
    Downward Movement: Decrease the underlying stock prices by the same percentages.

In [27]:
# Spot price multipliers
spot_price_multipliers = [0.80, 0.90, 0.95, 1.05, 1.1, 1.2]

# Compute the portfolio stats for each spot price multiplier
spot_price_analysis = f.analyze_spot_price_impact(
    portfolio_df=portfolio_df,
    spot_price_multipliers=spot_price_multipliers,
    process_portfolio_func=f.process_portfolio,
    compute_stats_func=f.compute_portfolio_stats
)

Analyzing spot price multiplier: 0.8
Adjusted spot prices:
0    355.2704
1    263.8848
2     16.4416
Name: spot_price, dtype: float64
Processed DataFrame:
   strike  lastPrice  impliedVolatility  expiration  time_to_expiration  \
0   630.0      67.25           0.140634  2024-12-27            0.093744   
1   375.0      21.50           0.214951  2026-06-18            1.567716   
2    37.0       0.61           0.263679  2026-06-18            1.567716   

   blackScholes_Price     delta          vega         gamma      theta  \
0          272.960327 -1.000000  5.071426e-37  3.047742e-40  18.846922   
1           99.190670 -0.840469  8.023742e+01  3.419333e-03   4.128616   
2            0.027615  0.015807  8.154953e-01  7.297773e-03  -0.075549   

          rho  type stock  spot_price  initial_weight  market_price  \
0  -58.892861   put  META    355.2704        0.000035         67.25   
1 -503.201834   put  MSFT    263.8848        0.000035         21.50   
2    0.364149  call   PFE     16.4

In [28]:
spot_price_analysis

total_delta     total_vega  total_gamma   total_theta      total_rho  \
0 -2065.860665  125249.106406    48.915639  22701.861712 -805621.432949   
1 -1748.592547  201405.660563    85.030677  15692.164025 -717203.222783   
2 -1549.555125  235760.819040   105.223124  12226.884477 -662778.985507   
3 -1086.685792  286345.534842   145.973693   6274.475453 -542146.432479   
4  -830.395194  300747.520262   165.003978   3987.675533 -479700.771659   
5  -286.436862  308794.662057   197.285209    857.772260 -358542.382833   

   total_expected_return  total_cost  spot_price_multiplier  
0          298180.989104     96435.0                   0.80  
1          220004.258567     96435.0                   0.90  
2          183565.950844     96435.0                   0.95  
3          116435.494269     96435.0                   1.05  
4           85724.213625     96435.0                   1.10  
5           29591.877769     96435.0                   1.20

## b. Implied Volatility Changes:

    Volatility Increase: Raise the implied volatility by 5%, 10%, 20%.
    Volatility Decrease: Lower the implied volatility by similar amounts.

In [29]:
# Implied volatility multipliers
volatility_multipliers = [0.80, 0.90, 0.95, 1.1, 1.2]

# Compute the portfolio stats for each implied volatility multiplier
implied_volatility_analysis = f.analyze_implied_volatility_impact(
    portfolio_df=portfolio_df,
    volatility_multipliers=volatility_multipliers,
    process_portfolio_func=f.process_portfolio,
    compute_stats_func=f.compute_portfolio_stats
)

In [30]:
implied_volatility_analysis

total_delta     total_vega  total_gamma   total_theta      total_rho  \
0 -1643.331512  248151.593514    78.473836  14184.222994 -625422.830731   
1 -1493.630922  256765.020043   104.205267  11634.547085 -613600.412973   
2 -1412.209424  260753.625475   115.609086  10343.352813 -608469.377861   
3 -1152.714823  271370.748481   142.426840   6433.823858 -595622.204632   
4  -974.523444  277314.901717   154.340699   3821.662207 -588869.562808   

   total_expected_return  total_cost  implied_volatility_multiplier  
0          137855.385726     96435.0                           0.80  
1          143344.348235     96435.0                           0.90  
2          146166.069367     96435.0                           0.95  
3          154912.059551     96435.0                           1.10  
4          160950.606143     96435.0                           1.20

## c. Time Passage:

    Advance Time: We simulate the passage of time (e.g., 7 days, 30 days, 60 days).

### 7 Days time

In [31]:
# Time increments in days
time_increments = [7, 30, 60]

# Compute the portfolio stats for each time increment
time_passage_analysis = f.analyze_time_passage_impact(
    portfolio_df=portfolio_df,
    time_increments=time_increments,
    update_time_func=f.update_time_to_expiration,
    process_portfolio_func=f.process_portfolio,
    compute_stats_func=f.compute_portfolio_stats
)

In [32]:
time_passage_analysis

total_delta     total_vega  total_gamma  total_theta      total_rho  \
0 -1342.794322  261980.568323   124.087327  9013.314544 -585415.937688   
1 -1386.140200  254609.435381   118.969604  8921.035144 -532566.310192   
2 -1442.742411  244766.119741   111.823360  8754.110033 -506366.119942   

   total_expected_return  total_cost  days_passed  
0          149234.998540     96435.0            7  
1          149800.078528     96435.0           30  
2          149230.409999     96435.0           60

## d. Combined Scenarios:

    Price and Volatility Shifts: Combine spot price changes with implied volatility adjustments.

In [33]:
# Define ranges
spot_price_multipliers = np.linspace(0.8, 1.2, 10)  # 10 evenly spaced points
volatility_multipliers = np.linspace(0.8, 1.2, 10)  # 10 evenly spaced points
time_increments = np.linspace(7, 60, 10, dtype=int)  # 10 points between 7 and 60

# Analyze the combined impact
combined_analysis = f.analyze_combined_impact(
    portfolio_df=portfolio_df,
    spot_price_multipliers=spot_price_multipliers,
    volatility_multipliers=volatility_multipliers,
    time_increments=time_increments,
    update_time_func=f.update_time_to_expiration,
    process_portfolio_func=f.process_portfolio,
    compute_stats_func=f.compute_portfolio_stats
)

In [34]:
combined_analysis

total_delta     total_vega  total_gamma   total_theta      total_rho  \
0   -2243.785340   83174.759373    15.930115  27429.334246 -818350.037325   
1   -2246.704725   81819.029480    15.471144  27493.462562 -804841.653739   
2   -2250.179832   80194.431344    14.930343  27571.129687 -788597.830592   
3   -2253.624172   78572.531439    14.400542  27649.583711 -772317.012582   
4   -2257.037688   76953.564431    13.881870  27728.833985 -755999.026765   
..           ...            ...          ...           ...            ...   
995   -23.179860  310685.611684   195.213188  -5146.930608 -306834.710097   
996   -37.411320  308710.816848   195.202664  -5277.205585 -303590.798802   
997   -51.758495  306721.853171   195.177023  -5409.217054 -300341.822037   
998   -66.222809  304718.516555   195.135606  -5543.007174 -297087.730784   
999   -80.805692  302700.598255   195.077721  -5678.619687 -293828.474820   

     total_expected_return  total_cost  spot_price_multiplier  \
0            294198.854806     96435.0                    0.8   
1            294575.037745     96435.0                    0.8   
2            295027.622375     96435.0                    0.8   
3            295481.490179     96435.0                    0.8   
4            295936.654172     96435.0                    0.8   
..                     ...         ...                    ...   
995           43042.912477     96435.0                    1.2   
996           42677.643530     96435.0                    1.2   
997           42310.218860     96435.0                    1.2   
998           41940.609578     96435.0                    1.2   
999           41568.786089     96435.0                    1.2   

     implied_volatility_multiplier  days_passed  
0                              0.8            7  
1                              0.8           12  
2                              0.8           18  
3                              0.8           24  
4                              0.8           30  
..                             ...          ...  
995                            1.2           36  
996                            1.2           42  
997                            1.2           48  
998                            1.2           54  
999                            1.2           60  

[1000 rows x 10 columns]

## 3. Data Visualization

### a. Total expected returns with respect to spot price and implied volatility changes

In [35]:
f.plot_interactive_3d_surface(
    data=combined_analysis,
    x_col="spot_price_multiplier",
    y_col="implied_volatility_multiplier",
    z_col="total_expected_return"
)


### b. Total Delta with respect to spot price changes and days passed

In [36]:
# Plot Delta
f.plot_interactive_3d_surface(
    data=combined_analysis,
    x_col="spot_price_multiplier",
    y_col="days_passed",
    z_col="total_delta"
)

### c. Total Vega with respect to implied volatility changes and days passed

In [37]:
# Plot Vega
f.plot_interactive_3d_surface(
    data=combined_analysis,
    x_col="implied_volatility_multiplier",
    y_col="days_passed",
    z_col="total_vega"
)

### d. Total Gamma with respect to spot price changes and days passed

In [38]:
# Plot Gamma
f.plot_interactive_3d_surface(
    data=combined_analysis,
    x_col="spot_price_multiplier",
    y_col="days_passed",
    z_col="total_gamma"
)


### e. TotalTheta with respect to spot price changes and days passed

In [39]:
# Plot Theta
f.plot_interactive_3d_surface(
    data=combined_analysis,
    x_col="spot_price_multiplier",
    y_col="days_passed",
    z_col="total_theta"
)

### f. Total Rho with respect to spot price changes and days passed

In [40]:
# Plot Rho
f.plot_interactive_3d_surface(
    data=combined_analysis,
    x_col="spot_price_multiplier",
    y_col="days_passed",
    z_col="total_rho"
)